In [1]:
!pip install --quiet sentence_transformers
print('installed sentence transformer package')

installed sentence transformer package


In [2]:
import pandas as pd
df = pd.read_csv(filepath_or_buffer='/kaggle/input/hate-speech-and-offensive-language-detection/train.csv')
df.sample(n=10, random_state=2023)

count  hate_speech_count  offensive_language_count  neither_count  \
12623      3                  1                         2              0   
10939      3                  0                         2              1   
12406      3                  0                         3              0   
21931      3                  0                         3              0   
4959       3                  2                         1              0   
18190      3                  0                         3              0   
8790       3                  1                         0              2   
14224      3                  0                         3              0   
24279      3                  0                         3              0   
13301      3                  1                         2              0   

       class                                              tweet  
12623      1  Lol when a nigga say he miss u say don't miss ...  
10939      1  I take it Notre Dame is still trash. http://t....  
12406      1  Light skin niccas always wanna try to be Ike T...  
21931      1  This biatch just called me a bitch &#128514;&#...  
4959       0  @TheRealJRSmith And its people like you that g...  
18190      1  RT @YoungGizzle_: First thing I look at is wha...  
8790       2  Don't dance, Iggy. It's trash just like your m...  
14224      1  RT @AshAmador: Started off with a OZ\nEnd up r...  
24279      1  no hoe shit or roxy shit but dawggg I swear I ...  
13301      1  Nigga, this bitch is scaring me. Pass me the b...

In [3]:
df.shape

(24783, 6)

In [4]:
import pandas as pd

df = df[['tweet']].drop_duplicates(ignore_index=True)
df['char count'] = df['tweet'].str.len()
df['word count'] = df['tweet'].apply(func=lambda x: len(x.split())) # word counts are approximate
print('one-token sentences: {}'.format(df[df['word count'] == 1]['tweet'].values.tolist()))
print('two-token sentences: {}'.format(df[df['word count'] == 2]['tweet'].values.tolist()))
print('we have {} sentences in our corpus.'.format(len(df)))

one-token sentences: ['#Yankees', '1-800-slap-a-hoe', 'bitches', 'bitches.', 'coons', 'pussy', 'retard.', 'u-bitch-u']
two-token sentences: ['#boom bitches', '#honeybadger bitch', '#wallofthewasatch bitch!', '&#128553; cunt', '@1000gramsBee bitch', '@1stBlock_Rody pussy', '@808NoHeartBreak hoes', '@AnthonyCumia pussy', '@AsapTwelvyy hoes.', '@Big_Jim777 bitch', '@BloodOfJupiter yeah...bitch!', '@CayMarieee bitch', '@Channnteeel pussy', '@CoreyRoyalty_ *hoes', '@DanielSizelove pussy', '@DevilElyie fag*', '@Dre_Day200 bitch', '@Eddie_Sativa87 pussy.', '@ElizabethBatman bitch.', '@EricWithAHotDad faggot', '@Fatass_mee pussy', '@FuckKennyJ trash', '@Fulf_ShawnFulf peckerwood', '@HarleyyyQuinn_ trash', '@Hovaa_ cracker....', '@Huntermoore nigger!!', '@IvetteBrianna_ fag', '@JOLTNG niger', '@JacobbBacker fag', '@JacobbBacker faggot', '@JadeGreenleaf fag', '@JaiBrooks1 faggot', '@JawShoeeAhhh *bitch', '@JjLoveUp tranny', '@Juice__2 faggot', '@King_4_Murphy pussy', '@KyleReinders bitch', '@Lil

In [5]:
from plotly.express import scatter
scatter(data_frame=df.sort_values(ascending=True, by='word count').reset_index(), y=['word count', 'char count']).show()
scatter(data_frame=df, x='word count', y='char count', hover_name='tweet', trendline='ols', log_x=True, log_y=True).show()

In [6]:
from arrow import now
from sentence_transformers import SentenceTransformer
MODELS = ['all-MiniLM-L12-v2', 'all-MiniLM-L6-v2',]
MODEL = MODELS[1] 
model_start = now()
model = SentenceTransformer(model_name_or_path=MODEL,)
# all our tweets are short so the default max sequence length should be adequated
print('model max sequence length: {}'.format(model.max_seq_length))
embeddings = model.encode(df['tweet'].values.tolist())
print('model time: {}'.format(now() - model_start))

.gitattributes:   0%|          | 0.00/1.18k [00:00<?, ?B/s]

1_Pooling/config.json:   0%|          | 0.00/190 [00:00<?, ?B/s]

README.md:   0%|          | 0.00/10.6k [00:00<?, ?B/s]

config.json:   0%|          | 0.00/612 [00:00<?, ?B/s]

config_sentence_transformers.json:   0%|          | 0.00/116 [00:00<?, ?B/s]

...

vocab.txt:   0%|          | 0.00/232k [00:00<?, ?B/s]

modules.json:   0%|          | 0.00/349 [00:00<?, ?B/s]

model max sequence length: 256


Batches:   0%|          | 0/775 [00:00<?, ?it/s]

model time: 0:03:00.264216


In [7]:
from nltk.tokenize import RegexpTokenizer
from plotly.colors import qualitative
from sklearn.feature_extraction.text import TfidfVectorizer

TOKENIZER = RegexpTokenizer(r'\w+')

# todo add singular/plural reconciliation

def find_term(arg:str, terms: list):
    lower = TOKENIZER.tokenize(text=arg.lower())
    for term in terms:
        if term in lower:
            return term
    return 'none'

DISCARD = {'just', 'rt' , 'http', 'like', 'don', 'yo', 'ain', 'bad', 'know', 'lol', 'love', 'amp', 'got'}
vectorizer = TfidfVectorizer(ngram_range=(1, 1), stop_words='english', max_df=0.5, min_df=0.01)
fit_result = vectorizer.fit_transform(raw_documents=df['tweet'].values)
word_weight_df = pd.DataFrame(data={'word': vectorizer.get_feature_names_out(), 'weight': fit_result.toarray().sum(axis=0),}).sort_values(ascending=False, by='weight')
# numeric values are emojis and we want to ignore them
terms = [word for word in word_weight_df.head(n=30)['word'].values.tolist() if word not in DISCARD and not word.isnumeric()]
terms += ['yankees', 'charlie', 'bird', 'yellow', 'ape']
print('top terms: {}'.format(sorted(terms)))

top terms: ['ape', 'ass', 'bird', 'bitch', 'bitches', 'charlie', 'faggot', 'fuck', 'fucking', 'hoe', 'hoes', 'nigga', 'niggas', 'pussy', 'shit', 'trash', 'yankees', 'yellow']


In [8]:
from plotly.express import bar
from umap import UMAP

umap_model = UMAP(n_components=2, random_state=2023, verbose=True, n_jobs=1)
df[['u0', 'u1']] = umap_model.fit_transform(X=embeddings)
df['term'] = df['tweet'].apply(func=find_term, args=(terms, ))
bar(data_frame=df['term'].value_counts().to_frame(), y='count', log_y=True)

UMAP(n_jobs=1, random_state=2023, verbose=True)
Sun Dec 24 22:33:22 2023 Construct fuzzy simplicial set
Sun Dec 24 22:33:22 2023 Finding Nearest Neighbors
Sun Dec 24 22:33:22 2023 Building RP forest with 13 trees
Sun Dec 24 22:33:26 2023 NN descent for 15 iterations
	 1  /  15
	 2  /  15
	 3  /  15
	 4  /  15
	 5  /  15
	 6  /  15
	 7  /  15
	 8  /  15
	Stopping threshold met -- exiting after 8 iterations
Sun Dec 24 22:33:42 2023 Finished Nearest Neighbor Search
Sun Dec 24 22:33:45 2023 Construct embedding


Epochs completed:   0%|            0/200 [00:00]

	completed  0  /  200 epochs
	completed  20  /  200 epochs
	completed  40  /  200 epochs
	completed  60  /  200 epochs
	completed  80  /  200 epochs
	completed  100  /  200 epochs
	completed  120  /  200 epochs
	completed  140  /  200 epochs
	completed  160  /  200 epochs
	completed  180  /  200 epochs
Sun Dec 24 22:33:57 2023 Finished embedding


In [9]:
from plotly.express import scatter
scatter(data_frame=df, x='u0', y='u1', hover_name='tweet', color='term', color_discrete_sequence=qualitative.Light24, height=800)

In [10]:
scatter(y=embeddings[2023])

In [11]:
scatter(y=model.encode('When I was your age I already had a job.'), log_y=False)

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

In [12]:
scatter(y=model.encode('When I was your age I already had a full-time job.'), log_y=False)

Batches:   0%|          | 0/1 [00:00<?, ?it/s]